In [ ]:
import rasterio
import numpy as np
import os
import pyproj

# Set up transformation from WGS84 (ellipsoidal) to EGM96 orthometric height
wgs84_ellipsoid = pyproj.CRS.from_epsg(4979)  # WGS84 + ellipsoidal height
egm96 = pyproj.CRS.from_string("+proj=latlong +datum=WGS84 +geoidgrids=egm96_15.gtx +type=crs")

transformer = pyproj.Transformer.from_crs(wgs84_ellipsoid, egm96, always_xy=True)

def egm96geoid(lat, lon):
    lon = float(lon)
    lat = float(lat)
    _, _, orthometric_height = transformer.transform(lon, lat, 0)
    # Geoid height is the difference between input height (0) and output orthometric
    return -orthometric_height

# Path to input and output files
input_tiff = #your DTM .tiff
output_tiff = #your output

print(f"Reading input file: {input_tiff}")

# Read the GeoTIFF file
with rasterio.open(input_tiff) as src:
    # Read the entire raster band
    A = src.read(1).astype('float64')  # Read as double precision float
    nodata_value = src.nodata if src.nodata is not None else -9999
    
    # Get dimensions and transformation
    height, width = A.shape
    transform = src.transform
    
    # Copy metadata for the output file
    profile = src.profile.copy()
    profile.update(dtype=rasterio.float64, nodata=nodata_value)
    
    # Create arrays to store lat/lon coordinates for each pixel
    lats = np.zeros((height, width))
    lons = np.zeros((height, width))
    
    # Calculate coordinates for each pixel
    for i in range(height):
        for j in range(width):
            # Get coordinates of the pixel center
            # +0.5 to get center of pixel (rasterio uses upper-left corner)
            lon, lat = transform * (j + 0.5, i + 0.5)
            lats[i, j] = lat
            lons[i, j] = lon
    
    # Initialize height array with the same shape as A
    h = np.zeros_like(A)
    
    # Apply the geoid correction to each pixel
    for i in range(height):
        for j in range(width):
            if A[i, j] <= nodata_value or np.isnan(A[i, j]):
                h[i, j] = nodata_value
            else:
                # Get geoid height (N) for this location
                N = egm96geoid(lats[i, j], lons[i, j])
                print(N)
                # Add the geoid height to the orthometric height to get ellipsoidal height
                # Ellipsoidal height (h) = Orthometric height (H) + Geoid height (N)
                h[i, j] = A[i, j] + N
                print(A[i, j])
                print(h[i, j])
    
    print(f"Writing output file: {output_tiff}")
    
    # Write the result to a new GeoTIFF file
    with rasterio.open(output_tiff, 'w', **profile) as dst:
        dst.write(h, 1)

print(f"Ellipsoidal height correction applied and saved to {output_tiff}")
print(f"Statistics: min={np.min(h[h > nodata_value]):.2f}, max={np.max(h[h > nodata_value]):.2f}, mean={np.mean(h[h > nodata_value]):.2f}")

Reading input file: C:\Users\fraot\Documents\Dottorato\EGU_2025\EGU\3D_Model\RS3\DTM_WGS84_clip.tif
41.07143027045999
0.546999990940094
41.618430261400086
41.07142200002566
0.2070000022649765
41.27842200229064
41.0715635340448
1.2359999418258667
42.307563475870666
41.07155526067543
0.9660000205039978
42.03755528117943
41.071546987306036
0.5669999718666077
41.63854695917264
41.071538713936654
0.22699999809265137
41.298538712029305
41.071530440567265
0.22699999809265137
41.29853043865992
41.07169680349974
3.4560000896453857
44.52769689314513
41.0716885271953
1.8860000371932983
42.9576885643886
41.071680250890864
1.1859999895095825
42.25768024040045
41.071671974586415
0.8759999871253967
41.94767196171181
41.07166369828197
0.5360000133514404
41.60766371163341
41.071655421977525
0.5360000133514404
41.607655435328965
41.07164714567308
0.3059999942779541
41.37764713995104
41.07163886936865
0.006000000052154064
41.0776388694208
41.07183007882499
5.8460001945495605
46.91783027337455
41.07182179